# # 모듈 및 함수
---

In [1]:
import os
import glob
import re
import json
import shutil
import numpy as np
import pandas as pd

# # data processing
---

In [2]:
# scenes = np.loadtxt('/NIA50/50-2/data/nia50_all/pvrcnn/ImageSets/test.txt', dtype=object).tolist()
scenes = sorted(os.listdir('/data/NIA50/50-2/result/deepfusionmot_allcat/image'))

## # gt
---

### # evaluate_tracking.seqmap.training
---

In [4]:
save_path = '/data/NIA50/50-2/data/NIA50/nia50_all/trackeval_allcat/gt/'
os.makedirs(save_path, exist_ok=True)

seqmap = [f'{scene} empty 0000 0010' for scene in scenes]
seqmap[0] = re.sub('0000', '0001', seqmap[0])

with open(save_path+'evaluate_tracking.seqmap.training', 'w') as f:
    f.write('\n'.join(seqmap))

In [ ]:
# # yolov5, pvrcnn inference 완료한 데이터

# with open('/data/NIA50/50-2/data/NIA50/학습용데이터_pre4/Suwon/ImageSets/test.txt', 'r') as f:
#     scenes = [re.sub('\n', '', i)[:-5] for i in f.readlines()]
#     scenes = sorted(list(set(scenes)))

In [ ]:
# # deepfusionmot 완료된 것만

# scenes = sorted(os.listdir('/data/NIA50/50-2/data/NIA50/train_1st/trackeval/trackers/nia50_train1st'))
# scenes = [i[:-4] for i in scenes]

### # label_02
---

In [7]:
save_path = '/data/NIA50/50-2/data/NIA50/nia50_all/trackeval_allcat/gt/label_02/'
os.makedirs(save_path, exist_ok=True)


# Z축 이동을 위해서 calib와 매칭하여 이동범위 지정
calibs = sorted(glob.glob('/NIA50/50-2/data/nia50_all/raw/*/calib/camera/camera_0.json'))
calib_ls = []
scenes = []
for calib in calibs:
    scene = re.findall('[a-zA-Z0-9_]+', calib)[-5]
    with open(calib, 'r') as f:
        calib = json.load(f)
    if calib['extrinsic'] not in calib_ls:
        calib_ls.append(calib['extrinsic'])
        scenes.append(scene)
    
calib_typ = {'typ1': {'calib': calib_ls[0], 'mov_zpoint': 14},
             'typ2': {'calib': calib_ls[1], 'mov_zpoint': 13},
             'typ3': {'calib': calib_ls[2], 'mov_zpoint': 0},
             'typ4': {'calib': calib_ls[3], 'mov_zpoint': -20}}

rename = {'Adult': 'Adult', 
          'Bus': 'Car',
          'Car': 'Car',
          'Kid': 'Kid',
          'Kickboard': 'Two_Wheeler',
          'Large_Truck': 'Car',
          'Light_Car': 'Car',
          'Medium_Truck': 'Car',
          'Mini_Bus': 'Car',
          'SUV': 'SUV',
          'Small_Car': 'Car',
          'Small_Truck': 'Car',
          'Special_Vehicle': 'Car',
          'Two_Wheeler': 'Two_Wheeler',
          'Van': 'Van'}

scenes = sorted(os.listdir('/NIA50/50-2/result/deepfusionmot/image'))
source_path = '/NIA50/50-2/data/nia50_all/raw/'
for scene in scenes:
    calib = source_path + scene + '/calib/camera/camera_0.json'
    with open(calib, 'r') as f:
        calib = json.load(f)
    intrinsic = np.asarray(calib['intrinsic']).reshape(3, 3)
    intrinsic = np.hstack([intrinsic, np.asarray([[0, 0, 0]]).reshape(-1, 1)])
    extrinsic = np.asarray(calib['extrinsic']).reshape(4, 4)
    
    labels = sorted(glob.glob(f'{source_path}/{scene}/label/[0-9]*.json'))
    # scene_df = pd.DataFrame(columns=['frame', 'track_id', 'type', 'truncated', 'occluded', 'alpha', 'bbox', 'dimensions', 'location', 'rotation_y'])
    frame = []
    track_id = []
    type_ = []

    x1, y1, x2, y2 = [], [], [], []
    h_, w_, l_ = [], [], []
    x_, y_, z_ = [], [], []
    rotation_y = []
    for i, label in enumerate(labels):
        with open(label, 'r') as f:
            label = json.load(f)
        
        check_id = []
        for obj in label:
            try:
                if obj['obj_id'] in set(check_id):
                    continue

                renamed_type = rename[obj['obj_type']]
                
                def roty(t, Rx=90/180*np.pi):
                    ''' Rotation about the y-axis. '''
                    c = np.cos(t)
                    s = np.sin(t)

                    X = np.array([[1, 0, 0],
                                    [0, np.cos(Rx), -np.sin(Rx)],
                                    [0, np.sin(Rx), np.cos(Rx)]])

                    # X = np.eye(3)

                    Z = np.array([[c, -s, 0],
                                    [s, c, 0],
                                    [0, 0, 1]])
                    
                    return np.matmul(Z, X)
                
                R = roty(obj['psr']['rotation']['z'])
                x = obj['psr']['position']['x']        
                y = obj['psr']['position']['y']        
                z = obj['psr']['position']['z']
                l = obj['psr']['scale']['x']
                w = obj['psr']['scale']['y']
                h = obj['psr']['scale']['z']
                
                x_corners = [l / 2, l / 2, -l / 2, -l / 2, l / 2, l / 2, -l / 2, -l / 2];
                y_corners = [h / 2, h / 2, h / 2, h / 2, -h / 2, -h / 2, -h / 2, -h / 2];
                z_corners = [w / 2, -w / 2, -w / 2, w / 2, w / 2, -w / 2, -w / 2, w / 2];
                
                corners_3d = np.dot(R, np.vstack([x_corners, y_corners, z_corners]))
                corners_3d[0, :] = corners_3d[0, :] + x  # x
                corners_3d[1, :] = corners_3d[1, :] + y  # y
                corners_3d[2, :] = corners_3d[2, :] + z  # z
                corners_3d = np.vstack([corners_3d, [1, 1, 1, 1, 1, 1, 1, 1]])
                
                point2d = np.matmul(intrinsic, np.matmul(extrinsic, corners_3d))
                pointx = np.around(point2d/point2d[2])[0]
                pointy = np.around(point2d/point2d[2])[1]
                pointx[pointx > 1920] = 1920
                pointx[pointx < 0] = 0
                pointy[pointy > 1200] = 1200
                pointy[pointy < 0] = 0
                
                if calib['extrinsic'] == calib_typ['typ1']['calib']: z += calib_typ['typ1']['mov_zpoint']
                elif calib['extrinsic'] == calib_typ['typ2']['calib']: z += calib_typ['typ2']['mov_zpoint']
                elif calib['extrinsic'] == calib_typ['typ3']['calib']: z += calib_typ['typ3']['mov_zpoint']
                elif calib['extrinsic'] == calib_typ['typ4']['calib']: z += calib_typ['typ4']['mov_zpoint']
                # xyxy = f'{min(pointx)} {min(pointy)} {max(pointx)} {max(pointy)}'
                frame.append(i)
                track_id.append(obj['obj_id'])
                check_id.append(obj['obj_id'])
                type_.append(renamed_type)
                h_.append(obj['psr']['scale']['z'])
                w_.append(obj['psr']['scale']['y'])
                l_.append(obj['psr']['scale']['x'])
                x_.append(obj['psr']['position']['x'])
                y_.append(obj['psr']['position']['y'])
                z_.append(z)
                rotation_y.append(obj['psr']['rotation']['z'])
                x1.append(min(pointx))
                y1.append(min(pointy))
                x2.append(max(pointx))
                y2.append(max(pointy))
            except:
                pass
            
    scene_df = pd.DataFrame(columns=['frame', 'track_id', 'type', 'truncated', 'occluded', 'alpha', 'x1', 'y1', 'x2', 'y2', 'h', 'w', 'l', 'x', 'y', 'z', 'rotation_y'])  
    scene_df[['frame', 'track_id', 'type', 'x1', 'y1', 'x2', 'y2', 'h', 'w', 'l', 'x', 'y', 'z', 'rotation_y']] = \
        np.asarray([frame, track_id, type_, x1, y1, x2, y2, h_, w_, l_, x_, y_, z_, rotation_y]).T
    scene_df[['truncated', 'occluded', 'alpha']] = 0
    scene_df[['x1', 'y1', 'x2', 'y2']] = scene_df[['x1', 'y1', 'x2', 'y2']].astype(float)
    # scene_df[['track_id']] = scene_df[['track_id']].astype(int)
    # scene_df = scene_df.loc[(scene_df['x2']-scene_df['x1']!=0) & (scene_df['y2']-scene_df['y1']!=0) & scene_df['track_id'].apply(lambda x: len(x)>0)]
    scene_df = scene_df.loc[(scene_df['x2']-scene_df['x1']!=0) & (scene_df['y2']-scene_df['y1']!=0) & (scene_df['track_id'].str.isnumeric())]
    
    scene_df.to_csv(save_path+f'{scene}.txt', index=None, header=None, sep=' ')

In [ ]:
# # yolov5, pvrcnn inference 완료한 데이터

# with open('/data/NIA50/50-2/data/NIA50/학습용데이터_pre4/Suwon/ImageSets/test.txt', 'r') as f:
#     scenes = [re.sub('\n', '', i)[:-5] for i in f.readlines()]
#     scenes = sorted(list(set(scenes)))

# save_path = '/data/NIA50/50-2/data/NIA50/train_1st/trackeval/gt/label_02/'
# os.makedirs(save_path, exist_ok=True)

# rename = {'Adult': 'Adult', 
#           'Bus': 'Car',
#           'Car': 'Car',
#           'Kid': 'Kid',
#           'Kickboard': 'Two_Wheeler',
#           'Large_Truck': 'Car',
#           'Light_Car': 'Car',
#           'Medium_Truck': 'Car',
#           'Mini_Bus': 'Car',
#           'SUV': 'SUV',
#           'Small_Car': 'Car',
#           'Small_Truck': 'Car',
#           'Special_Vehicle': 'Car',
#           'Two_Wheeler': 'Two_Wheeler',
#           'Van': 'Van'}


# source_path = '/data/NIA50/50-2/data/NIA50/train_1st/raw/'
# for scene in scenes:
#     calib = source_path + scene + '/calib/camera/camera_0.json'
#     with open(calib, 'r') as f:
#         calib = json.load(f)
#     intrinsic = np.asarray(calib['intrinsic']).reshape(3, 3)
#     intrinsic = np.hstack([intrinsic, np.asarray([[0, 0, 0]]).reshape(-1, 1)])
#     extrinsic = np.asarray(calib['extrinsic']).reshape(4, 4)
    
#     labels = sorted(glob.glob(f'{source_path}/{scene}/label/[0-9]*.json'))
#     # scene_df = pd.DataFrame(columns=['frame', 'track_id', 'type', 'truncated', 'occluded', 'alpha', 'bbox', 'dimensions', 'location', 'rotation_y'])
#     frame = []
#     track_id = []
#     type_ = []
#     # truncated = []
#     # occluded = []
#     # alpha = []
#     # bbox = []
#     # dimensions = []
#     # location = []
#     x1, y1, x2, y2 = [], [], [], []
#     h_, w_, l_ = [], [], []
#     x_, y_, z_ = [], [], []
#     rotation_y = []
#     for i, label in enumerate(labels):
#         with open(label, 'r') as f:
#             label = json.load(f)
        
#         check_id = []
#         for obj in label:
#             try:
#                 if obj['obj_id'] in set(check_id):
#                     continue
#                 #     continue
#                 # if obj['obj_type'] in rename.keys():
#                 # frame.append(i)
#                 # track_id.append(obj['obj_id'])
#                 renamed_type = rename[obj['obj_type']]
#                 # type_.append(renamed_type)
#                 # scale = obj['psr']['scale']
#                 # scale = f'{scale["z"]} {scale["y"]} {scale["x"]}'
#                 # dimensions.append(scale)
#                 # position = obj['psr']['position']
#                 # position = f'{position["x"]} {position["y"]} {position["z"]}'
#                 # location.append(position)
#                 # h_.append(obj['psr']['scale']['z'])
#                 # w_.append(obj['psr']['scale']['y'])
#                 # l_.append(obj['psr']['scale']['x'])
#                 # x_.append(obj['psr']['position']['x'])
#                 # y_.append(obj['psr']['position']['y'])
#                 # z_.append(obj['psr']['position']['z'])
#                 # rotation_y.append(obj['psr']['rotation']['z'])
                
#                 def roty(t, Rx=90/180*np.pi):
#                     ''' Rotation about the y-axis. '''
#                     c = np.cos(t)
#                     s = np.sin(t)

#                     X = np.array([[1, 0, 0],
#                                     [0, np.cos(Rx), -np.sin(Rx)],
#                                     [0, np.sin(Rx), np.cos(Rx)]])

#                     # X = np.eye(3)

#                     Z = np.array([[c, -s, 0],
#                                     [s, c, 0],
#                                     [0, 0, 1]])
                    
#                     return np.matmul(Z, X)
                
#                 R = roty(obj['psr']['rotation']['z'])
#                 x = obj['psr']['position']['x']        
#                 y = obj['psr']['position']['y']        
#                 z = obj['psr']['position']['z']
#                 l = obj['psr']['scale']['x']
#                 w = obj['psr']['scale']['y']
#                 h = obj['psr']['scale']['z']
                
#                 x_corners = [l / 2, l / 2, -l / 2, -l / 2, l / 2, l / 2, -l / 2, -l / 2];
#                 y_corners = [h / 2, h / 2, h / 2, h / 2, -h / 2, -h / 2, -h / 2, -h / 2];
#                 z_corners = [w / 2, -w / 2, -w / 2, w / 2, w / 2, -w / 2, -w / 2, w / 2];
                
#                 corners_3d = np.dot(R, np.vstack([x_corners, y_corners, z_corners]))
#                 corners_3d[0, :] = corners_3d[0, :] + x  # x
#                 corners_3d[1, :] = corners_3d[1, :] + y  # y
#                 corners_3d[2, :] = corners_3d[2, :] + z  # z
#                 corners_3d = np.vstack([corners_3d, [1, 1, 1, 1, 1, 1, 1, 1]])
                
#                 point2d = np.matmul(intrinsic, np.matmul(extrinsic, corners_3d))
#                 pointx = np.around(point2d/point2d[2])[0]
#                 pointy = np.around(point2d/point2d[2])[1]
#                 pointx[pointx > 1920] = 1920
#                 pointx[pointx < 0] = 0
#                 pointy[pointy > 1200] = 1200
#                 pointy[pointy < 0] = 0
                
#                 # xyxy = f'{min(pointx)} {min(pointy)} {max(pointx)} {max(pointy)}'
#                 frame.append(i)
#                 track_id.append(obj['obj_id'])
#                 check_id.append(obj['obj_id'])
#                 type_.append(renamed_type)
#                 h_.append(obj['psr']['scale']['z'])
#                 w_.append(obj['psr']['scale']['y'])
#                 l_.append(obj['psr']['scale']['x'])
#                 x_.append(obj['psr']['position']['x'])
#                 y_.append(obj['psr']['position']['y'])
#                 z_.append(obj['psr']['position']['z'])
#                 rotation_y.append(obj['psr']['rotation']['z'])
#                 x1.append(min(pointx))
#                 y1.append(min(pointy))
#                 x2.append(max(pointx))
#                 y2.append(max(pointy))
#             except:
#                 pass
            
#     scene_df = pd.DataFrame(columns=['frame', 'track_id', 'type', 'truncated', 'occluded', 'alpha', 'x1', 'y1', 'x2', 'y2', 'h', 'w', 'l', 'x', 'y', 'z', 'rotation_y'])  
#     scene_df[['frame', 'track_id', 'type', 'x1', 'y1', 'x2', 'y2', 'h', 'w', 'l', 'x', 'y', 'z', 'rotation_y']] = \
#         np.asarray([frame, track_id, type_, x1, y1, x2, y2, h_, w_, l_, x_, y_, z_, rotation_y]).T
#     scene_df[['truncated', 'occluded', 'alpha']] = 0
    
#     scene_df.to_csv(save_path+f'{scene}.txt', index=None, header=None, sep=' ')

## # trackers
---

In [8]:
source_path = '/NIA50/50-2/result/deepfusionmot/data'
save_path = '/NIA50/50-2/data/nia50_all/trackeval2/trackers/label_02'
os.makedirs(save_path, exist_ok=True)

shutil.copytree(source_path, save_path, dirs_exist_ok=True)

'/NIA50/50-2/data/nia50_all/trackeval2/trackers/label_02'

In [ ]:
# source_path = '/data/NIA50/50-2/models/DeepFusionMOT/results/nia50_train1st/data'
# save_path = '/data/NIA50/50-2/data/NIA50/train_1st/trackeval/trackers/nia50_train1st'
# os.makedirs(save_path, exist_ok=True)

# shutil.copytree(source_path, save_path, dirs_exist_ok=True)

# # evaluation
---

In [3]:
%cd /data/NIA50/50-2/models/TrackEval_aivill

# USE_PARALLEL = True
# NUM_PARALLEL_CORES = 4
# # CLASSES_TO_EVAL = ['Car', 'Pedestrian', 'Cyclist']
GT_FOLDER = '/data/NIA50/50-2/data/nia50_final/trackeval_integ_2_temp/gt'
TRACKERS_FOLDER = '/data/NIA50/50-2/data/nia50_final/trackeval_integ_2_temp/trackers'
OUTPUT_FOLDER = '/data/NIA50/50-2/result/trackeval_integ_2_temp'

!python scripts/run_kitti.py --GT_FOLDER {GT_FOLDER} --TRACKERS_FOLDER {TRACKERS_FOLDER} --OUTPUT_FOLDER {OUTPUT_FOLDER}

/data/NIA50/50-2/models/TrackEval_aivill
Error importing BURST due to missing underlying dependency: No module named 'pycocotools'

Eval Config:
USE_PARALLEL         : False                         
NUM_PARALLEL_CORES   : 8                             
BREAK_ON_ERROR       : True                          
RETURN_ON_ERROR      : False                         
LOG_ON_ERROR         : /data/NIA50/50-2/models/TrackEval_aivill/error_log.txt
PRINT_RESULTS        : True                          
PRINT_ONLY_COMBINED  : False                         
PRINT_CONFIG         : True                          
TIME_PROGRESS        : True                          
DISPLAY_LESS_PROGRESS : False                         
OUTPUT_SUMMARY       : True                          
OUTPUT_EMPTY_CLASSES : True                          
OUTPUT_DETAILED      : True                          
PLOT_CURVES          : True                          

Kitti2DBox Config:
PRINT_CONFIG         : True                          


In [9]:
%cd /NIA50/50-2/models/TrackEval

# USE_PARALLEL = True
# NUM_PARALLEL_CORES = 4
# # CLASSES_TO_EVAL = ['Car', 'Pedestrian', 'Cyclist']
GT_FOLDER = '/NIA50/50-2/data/nia50_all/trackeval2/gt'
TRACKERS_FOLDER = '/NIA50/50-2/data/nia50_all/trackeval2/trackers'
# TRACKER_SUB_FOLDER = 'trackers'
OUTPUT_FOLDER = '/NIA50/50-2/result/trackeval2'

!python scripts/run_kitti.py --GT_FOLDER {GT_FOLDER} --TRACKERS_FOLDER {TRACKERS_FOLDER} --OUTPUT_FOLDER {OUTPUT_FOLDER}

/NIA50/50-2/models/TrackEval

Eval Config:
USE_PARALLEL         : False                         
NUM_PARALLEL_CORES   : 8                             
BREAK_ON_ERROR       : True                          
RETURN_ON_ERROR      : False                         
LOG_ON_ERROR         : /NIA50/50-2/models/TrackEval/error_log.txt
PRINT_RESULTS        : True                          
PRINT_ONLY_COMBINED  : False                         
PRINT_CONFIG         : True                          
TIME_PROGRESS        : True                          
DISPLAY_LESS_PROGRESS : False                         
OUTPUT_SUMMARY       : True                          
OUTPUT_EMPTY_CLASSES : True                          
OUTPUT_DETAILED      : True                          
PLOT_CURVES          : True                          

Kitti2DBox Config:
PRINT_CONFIG         : True                          
GT_FOLDER            : /NIA50/50-2/data/nia50_all/trackeval2/gt
TRACKERS_FOLDER      : /NIA50/50-2/data/nia50_all/

In [60]:
%cd /NIA50/50-2/models/TrackEval

!python scripts/run_kitti.py --help

/NIA50/50-2/models/TrackEval
Error importing BURST due to missing underlying dependency: No module named 'pycocotools'
usage: run_kitti.py [-h] [--USE_PARALLEL USE_PARALLEL]
                    [--NUM_PARALLEL_CORES NUM_PARALLEL_CORES]
                    [--BREAK_ON_ERROR BREAK_ON_ERROR]
                    [--RETURN_ON_ERROR RETURN_ON_ERROR]
                    [--LOG_ON_ERROR LOG_ON_ERROR]
                    [--PRINT_RESULTS PRINT_RESULTS]
                    [--PRINT_ONLY_COMBINED PRINT_ONLY_COMBINED]
                    [--PRINT_CONFIG PRINT_CONFIG]
                    [--TIME_PROGRESS TIME_PROGRESS]
                    [--DISPLAY_LESS_PROGRESS DISPLAY_LESS_PROGRESS]
                    [--OUTPUT_SUMMARY OUTPUT_SUMMARY]
                    [--OUTPUT_EMPTY_CLASSES OUTPUT_EMPTY_CLASSES]
                    [--OUTPUT_DETAILED OUTPUT_DETAILED]
                    [--PLOT_CURVES PLOT_CURVES] [--GT_FOLDER GT_FOLDER]
                    [--TRACKERS_FOLDER TRACKERS_FOLDER]
              

# # result
---

In [3]:
import pandas as pd

car = pd.read_csv('/NIA50/50-2/result/trackeval/label_02/car_detailed.csv')
car[['seq', 'HOTA(0)', 'HOTA___AUC', 'MOTA', 'MOTP']]

seq   HOTA(0)  HOTA___AUC      MOTA      MOTP
0    L_2210_Suwon_A_A_C0004  0.659912    0.579938  0.434783  0.856301
1    L_2210_Suwon_A_A_C0006  0.728912    0.666582  0.546392  0.890468
2    L_2210_Suwon_A_A_C0020  0.546536    0.511567  0.309859  0.913054
3    L_2210_Suwon_A_A_C0021  0.665367    0.614438  0.451613  0.918891
4    L_2210_Suwon_A_A_C0036  0.408567    0.325823  0.078125  0.877408
..                      ...       ...         ...       ...       ...
667  L_2211_Suwon_B_F_C0992  0.698501    0.661734  0.354167  0.914113
668  L_2211_Suwon_B_F_C0995  0.474058    0.443717  0.195402  0.888635
669  L_2211_Suwon_B_F_C1000  0.226691    0.194485  0.125000  0.894886
670  L_2211_Suwon_B_F_C1001  0.347677    0.321712  0.090909  0.913298
671                COMBINED  0.552427    0.489754  0.239258  0.882478

[672 rows x 5 columns]

In [147]:
list(car.columns)

['seq',
 'HOTA(0)',
 'LocA(0)',
 'HOTALocA(0)',
 'HOTA___5',
 'HOTA___10',
 'HOTA___15',
 'HOTA___20',
 'HOTA___25',
 'HOTA___30',
 'HOTA___35',
 'HOTA___40',
 'HOTA___45',
 'HOTA___50',
 'HOTA___55',
 'HOTA___60',
 'HOTA___65',
 'HOTA___70',
 'HOTA___75',
 'HOTA___80',
 'HOTA___85',
 'HOTA___90',
 'HOTA___95',
 'HOTA___AUC',
 'DetA___5',
 'DetA___10',
 'DetA___15',
 'DetA___20',
 'DetA___25',
 'DetA___30',
 'DetA___35',
 'DetA___40',
 'DetA___45',
 'DetA___50',
 'DetA___55',
 'DetA___60',
 'DetA___65',
 'DetA___70',
 'DetA___75',
 'DetA___80',
 'DetA___85',
 'DetA___90',
 'DetA___95',
 'DetA___AUC',
 'AssA___5',
 'AssA___10',
 'AssA___15',
 'AssA___20',
 'AssA___25',
 'AssA___30',
 'AssA___35',
 'AssA___40',
 'AssA___45',
 'AssA___50',
 'AssA___55',
 'AssA___60',
 'AssA___65',
 'AssA___70',
 'AssA___75',
 'AssA___80',
 'AssA___85',
 'AssA___90',
 'AssA___95',
 'AssA___AUC',
 'DetRe___5',
 'DetRe___10',
 'DetRe___15',
 'DetRe___20',
 'DetRe___25',
 'DetRe___30',
 'DetRe___35',
 'DetRe_